<a href="https://colab.research.google.com/github/ayakow1/ttic31220-japanparliament-analysis/blob/main/contextualized_topic_models.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Enabling the GPU

First, you'll need to enable GPUs for the notebook:

- Navigate to Edit→Notebook Settings
- select GPU from the Hardware Accelerator drop-down

[Reference](https://colab.research.google.com/notebooks/gpu.ipynb)

# Installing Contextualized Topic Models

First, we install the contextualized topic model library

In [13]:
%%capture
!pip install contextualized-topic-models==2.5.0

In [14]:
%%capture
!pip install pyldavis

## Restart the Notebook

For the changes to take effect, we now need to restart the notebook.

From the Menu:

Runtime → Restart Runtime

# Data

We are going to need some data. You should upload a file with one document per line. We assume you haven't run any preprocessing script.

However, if you want to first test the model without uploading your data, you can simply use the test file I'm putting here

In [2]:
from google.colab import drive
drive.mount("/content/drive")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [3]:
import sqlite3
import pandas as pd
import numpy as np

In [4]:
conn = sqlite3.connect('/content/drive/MyDrive/議事録/raw_speech.db')

In [5]:
all = pd.read_sql_query(f'''SELECT * FROM raw_speech WHERE speech_date >= '2022-01-01' AND speech_date <= '2023-04-31' ''', conn)

In [6]:
docs = all['speech'].to_list()

In [7]:
conn.close()

In [12]:
conn = sqlite3.connect('/content/drive/MyDrive/議事録/speech.db')

In [9]:
all2 = pd.read_sql_query(f'''SELECT * FROM speech WHERE speech_date >= '2022-01-01' AND speech_date <= '2023-04-31' ''', conn)

In [10]:
all=all.merge(all2, on='id')

In [11]:
conn.close()

# Importing what we need

In [1]:
from contextualized_topic_models.models.ctm import ZeroShotTM, CombinedTM
from contextualized_topic_models.utils.data_preparation import TopicModelDataPreparation
from contextualized_topic_models.utils.preprocessing import WhiteSpacePreprocessingStopwords
import nltk

## Preprocessing （使わず）

Why do we use the **preprocessed text** here? We need text without punctuation to build the bag of word. Also, we might want only to have the most frequent words inside the BoW. Too many words might not help.

In [8]:
#  https://aidemy.net/magazine/688/
def sloth():
    import urllib3
    from bs4 import BeautifulSoup

    slothlib_path = 'http://svn.sourceforge.jp/svnroot/slothlib/CSharp/Version1/SlothLib/NLP/Filter/StopWord/word/Japanese.txt'
    http = urllib3.PoolManager()
    #↑urlib3系のおまじない
    slothlib_file =http.request('GET',slothlib_path)
    soup=BeautifulSoup(slothlib_file.data,'lxml')
    soup=str(soup).split()#soupは文字列じゃないので注意
    return soup

In [9]:
stopwords = sloth()

In [10]:
# from nltk.corpus import stopwords as stop_words

# nltk.download('stopwords')

# documents = [line.strip() for line in open(text_file, encoding="utf-8").readlines()[0:2000]]

# stopwords = list(stop_words.words("english"))

sp = WhiteSpacePreprocessingStopwords(docs, stopwords_list=stopwords)
preprocessed_documents, unpreprocessed_corpus, vocab, retained_indices = sp.preprocess()

In [11]:
preprocessed_documents[:2]

['早速 質問 入り ます 国会 とれ くらい 工事 示す 統計 この テータ あっ 問題 取り上け られ ます その によって gdp なっ たら 大きな 問題 てす この 問題 取り上け ます また 用い 見え くる 本年 賃上け 課題 について 考え たい 思い ます ます お手元 資料 年度 統計 という 記事 あり ます gdp 計算 ある 統計 総額 あり ます たた 数字 思え ます gdp 計算 なる すなわち ない 思う てす けれとも 国交省 お答え くたさい',
 'ハネル 今日 議員 お願い ます 少し 冒頭 いたたき 問題 なっ 統計 について 考え たい 思い ます ます そして なり ます てす 工事 総額 ヘース それから ヘース 工事 二つ ある 国交省 二つ とも 統計 取っ ます そして すれ あり ます けれとも 大体 年間 ヘース いう ほほ なる そういう ふう ます この 工事 示す 統計 てす 実は 多い また なく 一年 まとめ 調査 いい てす 統計 より 正確 てす たた gdp てき ませ なせ いう この 統計 という gdp 行い ます てす ほほ なきゃ いけ ない 一年 統計 てす さらに 一年 終わっ れる 更に 一年 なる のて gdp 用い られ ない gdp 用い られる 統計 なり ます 統計 ます のて くる gdp てきる てす しかしなから 調査 提出 なきゃ いか 大変 負担 てす てす 悪い てす ある てす 統計 すっと 少なく まて てす てす 工事 総額 として 使う てき ない そういう 統計 あり てす 使わ いう とれ くらい その いる それから あるいは さらに 民間 その という てきる てす 総務省 出し ます 日本 統計 この 統計 ます 統計 として ます そして この gdp 使わ くる という てす しゃ 元々 使う という てす 決算 ヘース 建設 数字 なり ます たた 決算 ヘース という さっき 工事 より より てす 三年 ます てす 三年 その 決算 ヘース 建設 投資 三年 工事 今年 工事 この せる によって 今年 gdp なる 建設 投資 する という まて 作業 てし てす 実際 その 工事 幾ら なる という 余り ない 統計 たっ

We don't discard the non-preprocessed texts, because we are going to use them as input for obtaining the contextualized document representations. 

Let's pass our files with preprocess and unpreprocessed data to our `TopicModelDataPreparation` object. This object takes care of creating the bag of words for you and of obtaining the contextualized BERT representations of documents. This operation allows us to create our training dataset.

Note: Here we use the contextualized model "distiluse-base-multilingual-cased", because we need a multilingual model for performing cross-lingual predictions later.  

Let's check the first ten words of the vocabulary 

## Training our Zero-Shot Contextualized Topic Model

Finally, we can fit our new topic model. We will ask the model to find 50 topics in our collection (n_component parameter of the CTM object).

In [15]:
tp = TopicModelDataPreparation("colorfulscoop/sbert-base-ja") #SBERTならなんでも対応：https://huggingface.co/colorfulscoop/sbert-base-ja

training_dataset = tp.fit(text_for_contextual=all['speech_x'].to_list(), text_for_bow=all['speech_y'].to_list())

/usr/local/lib/python3.10/dist-packages/contextualized_topic_models/utils/data_preparation.py:64: UserWarning: the longest document in your collection has 6474 words, the model instead truncates to 128 tokens.
  warnings.warn(


Batches:   0%|          | 0/246 [00:00<?, ?it/s]

In [17]:
import pickle

filehandler = open('/content/drive/MyDrive/議事録/tp.obj', 'wb') 
pickle.dump(tp, filehandler)

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [16]:
tp.vocab[:10]

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


array(['11基', '11発', '13デイズ', '18戦', '1ldk', '1号', '1系', '21世紀',
       '21世紀政策研究所', '2プラス2'], dtype=object)

In [18]:
ctm = ZeroShotTM(bow_size=len(tp.vocab), contextual_size=768, n_components=50, num_epochs=20)
ctm.fit(training_dataset) # run the model

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
Epoch: [20/20]	 Seen Samples: [980480/981320]	Train Loss: 526.2969484254523	Time: 0:00:09.229441: : 20it [03:01,  9.06s/it]
100%|██████████| 767/767 [00:07<00:00, 108.79it/s]


# Topics

After training, now it is the time to look at our topics: we can use the 

```
get_topic_lists
```

function to get the topics. It also accepts a parameter that allows you to select how many words you want to see for each topic.

In [19]:
ctm.get_topic_lists(5)

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


[['事故', '原発', '住民', '避難', '国交省'],
 ['土地', '所有者', '不明', '市町村', '計画'],
 ['社民', '結党', '今期', '濃密', '諸君'],
 ['融資', '財務省', '金融機関', '課税', '税収'],
 ['我が国', '安定', '取組', '重要', '安全保障'],
 ['ガス', 'ガソリン', 'カーボンニュートラル', '電力', 'lng'],
 ['入管', '事務所', '局長', 'ウィシュマ', '警察'],
 ['アメリカ', '中国', '交渉', '外務省', '台湾'],
 ['ワクチン', '接種', '承認', '開発', '医薬品'],
 ['原子力', '原発', '運転', '稼働', '発電'],
 ['お知らせ', '選任', '議事', '主宰', '指名'],
 ['元総理', '国葬', '拉致問題', '安倍', '統一協会'],
 ['コロナ', '対策', '補正予算', '賃上げ', '総理'],
 ['措置', '承認', '制度', '医薬品', '提供'],
 ['手当', '給与', '国家公務員', '雇用', '労働'],
 ['員数', '結党', '結び', '戦禍', '加速度'],
 ['議論', '憲法', '機能', '選挙', 'オンライン'],
 ['法律案', '趣旨', '措置', '附帯決議', '推進'],
 ['物価', '賃金', '円安', '上昇', 'gdp'],
 ['ウクライナ', '侵攻', 'ロシア', '侵略', '情勢'],
 ['安全保障', '経済', '国民', '我が国', '政府'],
 ['大変', '万博', '機会', '質問', 'お願い'],
 ['問題', '寄附', '法案', '献金', '被害者'],
 ['教員', '文科省', '研修', '学校', '授業'],
 ['結党', 'cs', '今月末', 'なおざり', '胃がん'],
 ['料金', '電動', '携帯電話', '自動車', '通信'],
 ['支援', '質問', '方々', '地域', '必要'],
 ['今期', '柔らか', '両県', '結党', '結び'],
 ['出

# Let's Draw!

We can use PyLDAvis to plot our topic in a nice and friendly manner :)

In [21]:
 lda_vis_data = ctm.get_ldavis_data_format(tp.vocab, training_dataset, n_samples=20)

100%|██████████| 767/767 [00:07<00:00, 99.74it/s] 


In [22]:
import pyLDAvis as vis
movies_pd = vis.prepare(**lda_vis_data)
vis.display(movies_pd)

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


# Topic Predictions

Ok now we can take a document and see which topic has been assigned to it. Results will obviously change with respect to the documents you are using. For example, let's predict the topic of the first preprocessed document that is talking about a peninsula.

In [43]:
topics_predictions = ctm.get_thetas(training_dataset, n_samples=50) # get all the topic predictions

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
100%|██████████| 767/767 [00:07<00:00, 98.27it/s] 


In [54]:
all['speech_x'].to_list()[1230] # see the text of our preprocessed document

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


'是非 これ は 国 が 積極的 に 協議 の 場 づくり に 関わっ て いく 、 まず そこ から 始め て いく こと が 大事 だ と 思っ て おり ます 。 そして 、 今 質疑 時間 終了 という こと で ござい ます ので 、 いろいろ と 災害 に 備え た 道路 ネットワーク が 大事 だ 、 しっかり 整備 し 、 国土 強靱 化 の 次期 計画 を しっかり 作る という こと 、 あるいは 観光振興 について も 、 旅行 支援 、 年明け の 一月 から の 閑散 期 も ターゲット に 進める べき 、 さらに は 、 知床 観光 船 事故 を 含め た 小型 観光 船 の 安全対策 や 観光バス の 安全対策 、 こうした 質問 も 用意 し て おり まし た が 、 是非 また しっかり 進め て いただく こと を お願い を いたし まし て 、 また 次 の 機会 に 改め させ て いただけれ ば と 思っ て おり ます 。 今日 は 充実 し た 質疑 を さ せ て いただき 、 ありがとう ござい まし た 。 終わり ます 。'

In [56]:
topic_number = np.argmax(topics_predictions[1230]) # get the topic id of the first document

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [58]:
ctm.get_topic_lists(10)[topic_number] #and the topic should be about natural location related things

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


['災害', '復興', '地震', '発生', '東日本大震災', '防災', '被災', '福島', '盛土', '建設']

## Training our Combined TM

Finally, we can fit our new topic model. We will ask the model to find 50 topics in our collection.

In [59]:
ctm2 = CombinedTM(bow_size=len(tp.vocab), contextual_size=768, n_components=20, num_epochs=10)
ctm2.fit(training_dataset) # run the model

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
Epoch: [10/10]	 Seen Samples: [490240/490660]	Train Loss: 516.4396264696246	Time: 0:00:11.309932: : 10it [01:54, 11.44s/it]
100%|██████████| 767/767 [00:07<00:00, 100.61it/s]


In [61]:
ctm2.get_topic_lists(5)

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


[['農業', '農家', '価格', '農地', '賃金'],
 ['消費者', '法律案', '法律', '措置', '改正'],
 ['質問', '日本', 'ウクライナ', '状況', '総理'],
 ['訓練', 'ミサイル', '攻撃', '米軍', '外務大臣'],
 ['政府', '確保', '対策', '対応', '必要'],
 ['憲法', '国会', '議論', '議員', '発言'],
 ['いか', '主宰', 'ないじゃないですか', '遺骨', 'ばか'],
 ['接種', 'ワクチン', 'オミクロン', '患者', '治療'],
 ['果敢', '包摂', '行政監視委員会', '結党', 'ベスト'],
 ['裁判', '法務省', '裁判所', '弁護士', '戸籍'],
 ['必要', '政府', '法案', '問題', '質問'],
 ['貴重', '統一教会', '副大臣', '政務官', '官房長官'],
 ['両者', '原点', '包摂', 'ウィズ', '自公政権'],
 ['資本主義', '総裁', '中国', 'アメリカ', '原子力'],
 ['学校', '子供たち', '文科省', '大学', '先生'],
 ['農水省', '有機', '有機農業', 'co2', 'ガソリン'],
 ['国交省', '工事', '道路', '国土交通省', '交通'],
 ['マイナンバーカード', '診療報酬', '処方箋', '検査', '保険証'],
 ['農地', '集積', '農業委員会', '有機農業', '担い手'],
 ['行財政改革', '包摂', '長い間', '一定の評価', '結党']]

In [62]:
topics_predictions = ctm2.get_thetas(training_dataset, n_samples=50) # get all the topic predictions

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
100%|██████████| 767/767 [00:07<00:00, 100.57it/s]


In [63]:
topic_number = np.argmax(topics_predictions[1230]) # get the topic id of the first document

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [64]:
ctm2.get_topic_lists(10)[topic_number] #and the topic should be about natural location related things

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


['国交省', '工事', '道路', '国土交通省', '交通', '交付税', '土砂', '監査', '地方交付税', '地震']

# Save Our Model for Later Use

In [65]:
ctm.save(models_dir="/content/drive/MyDrive/議事録/")
ctm2.save(models_dir="/content/drive/MyDrive/議事録/")

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
/usr/local/lib/python3.10/dist-packages/contextualized_topic_models/models/ctm.py:640: Warning: This is an experimental feature that we has not been fully tested. Refer to the following issue:https://github.com/MilaNLProc/contextualized-topic-models/issues/38
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/contextualized_topic_models/models/ctm.py:640: Warning: This is an experimental feature that we has not been fully tested. Refer to the following issue:https://github.com/MilaNLProc/contextualized-topic-models/issues/38
  warnings.warn(


In [68]:
# let's remove the trained model
del ctm
del ctm2

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [67]:

ctm = CombinedTM(bow_size=len(tp.vocab), contextual_size=768, num_epochs=100, n_components=50)

ctm.load("/content/drive/MyDrive/議事録/contextualized_topic_model_nc_50_tpm_0.0_tpv_0.98_hs_prodLDA_ac_(100, 100)_do_softplus_lr_0.2_mo_0.002_rp_0.99",
                                                                                                      epoch=19)

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
/usr/local/lib/python3.10/dist-packages/contextualized_topic_models/models/ctm.py:669: Warning: This is an experimental feature that we has not been fully tested. Refer to the following issue:https://github.com/MilaNLProc/contextualized-topic-models/issues/38
  warnings.warn(
